In [1]:
from pathlib import Path
from fishsense_api_sdk.client import Client
from synology_api.filestation import FileStation
from fishsense_data_processing_workflow_worker.config import settings
from urllib.parse import urlparse
from tqdm.asyncio import tqdm_asyncio
from tqdm.notebook import tqdm
import cv2
from fishsense_core.image.raw_image import RawImage
from fishsense_core.image.rectified_image import RectifiedImage

In [2]:
DIVE_ID = 393

In [3]:
DATA_FOLDER = (Path("../data") / "REEF" / "data").absolute()
OUTPUT_FOLDER = (Path("../output") / "preprocess_jpeg").absolute()

DATA_FOLDER.mkdir(parents=True, exist_ok=True)
OUTPUT_FOLDER.mkdir(parents=True, exist_ok=True)

DATA_FOLDER.exists(), OUTPUT_FOLDER.exists()

(True, True)

In [4]:
parsed_url = urlparse(settings.e4e_nas.url)

filestation = FileStation(parsed_url.hostname, parsed_url.port, settings.e4e_nas.username, settings.e4e_nas.password, secure=True, cert_verify=False)

User logged in, new session started!


In [5]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    dives = await client.dives.get_canonical()

len(dives), dives

(272,
 [Dive(id=1, name='080123_FSL-01 Photos', path='2023-09-07 REEF Data Dump/080123_FSL-01 Photos', dive_datetime=datetime.datetime(2023, 8, 1, 12, 46, 27, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=True, camera_id=1, dive_slate_id=1),
  Dive(id=5, name='Hogfish01_MolHITW_0926_080323', path='2023.08.03.FishSense.FSL-01D/Hogfish01_MolHITW_0926_080323', dive_datetime=datetime.datetime(2023, 8, 3, 9, 27, 23, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=None, camera_id=1, dive_slate_id=None),
  Dive(id=8, name='DogSnapper01_MolPeLe_1024_080323', path='2023.08.03.FishSense.FSL-01D/DogSnapper01_MolPeLe_1024_080323', dive_datetime=datetime.datetime(2023, 8, 3, 10, 24, 59, tzinfo=TzInfo(0)), priority=<Priority.LOW: 'LOW'>, flip_dive_slate=None, camera_id=1, dive_slate_id=None),
  Dive(id=14, name='Hogfish01_ConchLed_1419_080323', path='2023.08.03.FishSense.FSL-01D/Hogfish01_ConchLed_1419_080323', dive_datetime=datetime.datetime(2023, 8, 3, 14, 1

In [6]:
high_priority_dives = [dive for dive in dives if dive.priority == "HIGH"]

len(high_priority_dives), high_priority_dives

(9,
 [Dive(id=279, name='111323_Alligator DeepEast Drift2_FSL05', path='drive-download-20240307T1050Z/112023_Alligator/111323_Alligator/111323_Alligator_FSL05/111323_Alligator DeepEast Drift2_FSL05', dive_datetime=datetime.datetime(2023, 11, 13, 12, 34, 8, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=5, dive_slate_id=7),
  Dive(id=341, name='031424_Alligator0_FSL01', path='2024.06.20.REEF/03_2024_Alligator/031424_Alligator_FSL01/031424_Alligator0_FSL01', dive_datetime=datetime.datetime(2024, 3, 13, 23, 59, 45, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=1, dive_slate_id=8),
  Dive(id=347, name='031424_Alligator0_FSL02', path='2025-02-10 REEF Data Dump SMILE 6/031424_Alligator_FSL02/031424_Alligator0_FSL02', dive_datetime=datetime.datetime(2024, 3, 14, 12, 15, 46, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=2, dive_slate_id=11),
  Dive(id=349, name='031424_Alligator0

In [7]:
dives_by_id = {dive.id: dive for dive in high_priority_dives}

len(dives_by_id), dives_by_id

(9,
 {279: Dive(id=279, name='111323_Alligator DeepEast Drift2_FSL05', path='drive-download-20240307T1050Z/112023_Alligator/111323_Alligator/111323_Alligator_FSL05/111323_Alligator DeepEast Drift2_FSL05', dive_datetime=datetime.datetime(2023, 11, 13, 12, 34, 8, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=5, dive_slate_id=7),
  341: Dive(id=341, name='031424_Alligator0_FSL01', path='2024.06.20.REEF/03_2024_Alligator/031424_Alligator_FSL01/031424_Alligator0_FSL01', dive_datetime=datetime.datetime(2024, 3, 13, 23, 59, 45, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=1, dive_slate_id=8),
  347: Dive(id=347, name='031424_Alligator0_FSL02', path='2025-02-10 REEF Data Dump SMILE 6/031424_Alligator_FSL02/031424_Alligator0_FSL02', dive_datetime=datetime.datetime(2024, 3, 14, 12, 15, 46, tzinfo=TzInfo(0)), priority=<Priority.HIGH: 'HIGH'>, flip_dive_slate=None, camera_id=2, dive_slate_id=11),
  349: Dive(id=349, nam

In [8]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    existing_laser_labels = await tqdm_asyncio.gather(*[client.labels.get_laser_labels(dive.id) for dive in high_priority_dives])
    existing_laser_labels = [label for sublist in existing_laser_labels for label in sublist]


len(existing_laser_labels), existing_laser_labels

100%|██████████| 9/9 [00:01<00:00,  7.30it/s]


(1248,
 [LaserLabel(id=68291, label_studio_task_id=222285, label_studio_project_id=57, x=1906.7452918533202, y=1108.7285443467474, label='Red Laser', updated_at=datetime.datetime(2025, 10, 21, 1, 56, 10, 528749, tzinfo=TzInfo(0)), superseded=False, completed=True, label_studio_json={'annotations': [{'id': 118023, 'result': [{'id': 'result1', 'type': 'keypointlabels', 'value': {'x': 47.50237398737718, 'y': 36.76155651017067, 'width': 0.2, 'keypointlabels': ['Red Laser']}, 'origin': 'prediction', 'to_name': 'image', 'from_name': 'laser', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}, {'id': 'TggcHh6U8E', 'type': 'taxonomy', 'value': {'taxonomy': [['Fish']]}, 'origin': 'manual', 'to_name': 'image', 'from_name': 'species'}, {'id': '7BdA2E4RbZ', 'type': 'taxonomy', 'value': {'taxonomy': [['yes, center of fish']]}, 'origin': 'manual', 'to_name': 'image', 'from_name': 'measurable'}, {'id': 'wsFwM2z9kb', 'type': 'taxonomy', 'value': {'taxonomy': [['x < 5°']]}, 'origin':

In [9]:
laser_labels_by_image_id = {label.image_id: label for label in existing_laser_labels}

len(laser_labels_by_image_id), laser_labels_by_image_id

(1248,
 {78699: LaserLabel(id=68291, label_studio_task_id=222285, label_studio_project_id=57, x=1906.7452918533202, y=1108.7285443467474, label='Red Laser', updated_at=datetime.datetime(2025, 10, 21, 1, 56, 10, 528749, tzinfo=TzInfo(0)), superseded=False, completed=True, label_studio_json={'annotations': [{'id': 118023, 'result': [{'id': 'result1', 'type': 'keypointlabels', 'value': {'x': 47.50237398737718, 'y': 36.76155651017067, 'width': 0.2, 'keypointlabels': ['Red Laser']}, 'origin': 'prediction', 'to_name': 'image', 'from_name': 'laser', 'image_rotation': 0, 'original_width': 4014, 'original_height': 3016}, {'id': 'TggcHh6U8E', 'type': 'taxonomy', 'value': {'taxonomy': [['Fish']]}, 'origin': 'manual', 'to_name': 'image', 'from_name': 'species'}, {'id': '7BdA2E4RbZ', 'type': 'taxonomy', 'value': {'taxonomy': [['yes, center of fish']]}, 'origin': 'manual', 'to_name': 'image', 'from_name': 'measurable'}, {'id': 'wsFwM2z9kb', 'type': 'taxonomy', 'value': {'taxonomy': [['x < 5°']]}, 'o

In [10]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    dive_images = await client.images.get(dive_id=DIVE_ID)

len(dive_images), dive_images

(241,
 [Image(id=113697, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270091.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 51, tzinfo=TzInfo(0)), checksum='3c2e38a56aca2535ce2471b089e8bfcc', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113698, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270094.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='9f1801d273ecc9c4b1746a58b946252d', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113699, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270093.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='4c9e18af6f7d815976f476fe240a277d', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113700, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270092.ORF', taken_

In [11]:
incomplete_images = [image for image in dive_images if laser_labels_by_image_id.get(image.id) is None or not laser_labels_by_image_id[image.id].completed]

len(incomplete_images), incomplete_images

(211,
 [Image(id=113698, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270094.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='9f1801d273ecc9c4b1746a58b946252d', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113700, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270092.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='e29a3ef90e913653dd2acc1e3ec410f5', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113701, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270095.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 58, tzinfo=TzInfo(0)), checksum='a619b9bd3d1a776b3808737f50b2f7e0', is_canonical=True, dive_id=393, camera_id=1),
  Image(id=113702, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270096.ORF', taken_

In [12]:
image_by_id = {image.id: image for image in incomplete_images}

len(image_by_id), image_by_id

(211,
 {113698: Image(id=113698, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270094.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='9f1801d273ecc9c4b1746a58b946252d', is_canonical=True, dive_id=393, camera_id=1),
  113700: Image(id=113700, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270092.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 52, tzinfo=TzInfo(0)), checksum='e29a3ef90e913653dd2acc1e3ec410f5', is_canonical=True, dive_id=393, camera_id=1),
  113701: Image(id=113701, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alligator1_FSL01/P6270095.ORF', taken_datetime=datetime.datetime(2024, 6, 27, 21, 58, 58, tzinfo=TzInfo(0)), checksum='a619b9bd3d1a776b3808737f50b2f7e0', is_canonical=True, dive_id=393, camera_id=1),
  113702: Image(id=113702, path='2025-02-10 REEF Data Dump SMILE 6/062824_Alligator_FSL01/062824_Alliga

In [13]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    cameras = await tqdm_asyncio.gather(*[client.cameras.get(dive.camera_id) for dive in high_priority_dives])

len(cameras), cameras

100%|██████████| 9/9 [00:00<00:00, 33.37it/s]


(9,
 [Camera(id=5, serial_number='BJ6C67988', name='FSL-05'),
  Camera(id=1, serial_number='BJ6C69506', name='FSL-01'),
  Camera(id=2, serial_number='BJ6C83748', name='FSL-02'),
  Camera(id=6, serial_number='BJ6C67987', name='FSL-06'),
  Camera(id=3, serial_number='BJ6C85528', name='FSL-03'),
  Camera(id=1, serial_number='BJ6C69506', name='FSL-01'),
  Camera(id=4, serial_number='BJ6C85524', name='FSL-04'),
  Camera(id=6, serial_number='BJ6C67987', name='FSL-06'),
  Camera(id=3, serial_number='BJ6C85528', name='FSL-03')])

In [14]:
cameras_by_id = {camera.id: camera for camera in cameras}

len(cameras_by_id), cameras_by_id

(6,
 {5: Camera(id=5, serial_number='BJ6C67988', name='FSL-05'),
  1: Camera(id=1, serial_number='BJ6C69506', name='FSL-01'),
  2: Camera(id=2, serial_number='BJ6C83748', name='FSL-02'),
  6: Camera(id=6, serial_number='BJ6C67987', name='FSL-06'),
  3: Camera(id=3, serial_number='BJ6C85528', name='FSL-03'),
  4: Camera(id=4, serial_number='BJ6C85524', name='FSL-04')})

In [15]:
async with Client(settings.fishsense_api.url, settings.fishsense_api.username, settings.fishsense_api.password) as client:
    camera_intrinsics_list = await tqdm_asyncio.gather(*[client.cameras.get_intrinsics(camera.id) for camera in cameras])

len(camera_intrinsics_list), camera_intrinsics_list

100%|██████████| 9/9 [00:00<00:00, 25.68it/s]


(9,
  <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x79090004a580>])

In [16]:
camera_intrinsics_by_camera_id = {intrinsics.camera_id: intrinsics for intrinsics in camera_intrinsics_list}

len(camera_intrinsics_by_camera_id), camera_intrinsics_by_camera_id

(6,
 {5: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x79090005a570>,
  1: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x7908fdf28180>,
  2: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x7909000106e0>,
  6: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x79090004a250>,
  3: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x79090004a580>,
  4: <fishsense_api_sdk.models.camera_intrinsics.CameraIntrinsics at 0x7908fdf29350>})

In [18]:
for image in tqdm(incomplete_images):
    dive = dives_by_id[image.dive_id]
    camera = cameras_by_id[dive.camera_id]
    camera_intrinsics = camera_intrinsics_by_camera_id[camera.id]

    image_path = DATA_FOLDER / image.path
    target_path = OUTPUT_FOLDER / f"{image.checksum}.JPG"

    source_nas_path = f"/fishsense_data/REEF/data/{image.path}"
    filestation.get_file(source_nas_path, "download", dest_path=str(image_path.parent))

    image = RectifiedImage(RawImage(image_path), camera_intrinsics)
    img = image.data

    cv2.imwrite(target_path.as_posix(), img)

    target_nas_path = f"/fishsense_process_work/preprocess_jpeg"
    filestation.upload_file(target_nas_path, str(target_path), overwrite=True)

  0%|          | 0/211 [00:00<?, ?it/s]

<MultipartEncoder: {'path': '/fishsense_process_work/preprocess_jpeg', 'create_parents': 'true', 'overwrite': 'true', 'size': '7779018', 'files': ('9f1801d273ecc9c4b1746a58b946252d.JPG', <_io.BufferedReader name='/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/output/preprocess_jpeg/9f1801d273ecc9c4b1746a58b946252d.JPG'>, 'image/jpeg')}>





















































Upload Progress: 100%|██████████| 7.42M/7.42M [00:09<00:00, 863kB/s]


<MultipartEncoder: {'path': '/fishsense_process_work/preprocess_jpeg', 'create_parents': 'true', 'overwrite': 'true', 'size': '7735354', 'files': ('e29a3ef90e913653dd2acc1e3ec410f5.JPG', <_io.BufferedReader name='/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/output/preprocess_jpeg/e29a3ef90e913653dd2acc1e3ec410f5.JPG'>, 'image/jpeg')}>

































Upload Progress: 100%|██████████| 7.38M/7.38M [00:06<00:00, 1.14MB/s]


...




















Upload Progress: 100%|██████████| 7.33M/7.33M [00:04<00:00, 1.72MB/s]


<MultipartEncoder: {'path': '/fishsense_process_work/preprocess_jpeg', 'create_parents': 'true', 'overwrite': 'true', 'size': '7676121', 'files': ('5d32bf0f2ca7cd1e10a70d528088a300.JPG', <_io.BufferedReader name='/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/output/preprocess_jpeg/5d32bf0f2ca7cd1e10a70d528088a300.JPG'>, 'image/jpeg')}>




























Upload Progress: 100%|██████████| 7.32M/7.32M [00:04<00:00, 1.83MB/s]


<MultipartEncoder: {'path': '/fishsense_process_work/preprocess_jpeg', 'create_parents': 'true', 'overwrite': 'true', 'size': '7649838', 'files': ('0ad6d31aa67ad58a3ebdc680af3a7ff0.JPG', <_io.BufferedReader name='/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/output/preprocess_jpeg/0ad6d31aa67ad58a3ebdc680af3a7ff0.JPG'>, 'image/jpeg')}>






























Upload Progress: 100%|██████████| 7.30M/7.30M [00:04<00:00, 1.77MB/s]
